### OSMGetPOI.jl Tutorial
Full documentation: https://github.com/mkloe/OSMgetPOI

In [28]:
using OSMgetPOI

### 1. Download .osm data file
- Downloading from Geofabrik
    1. Go to https://download.bbbike.org/osm/bbbike/ and select a city.
    2. Copy URL of *OSM XML gzip'd* file (exemplary URL: https://download.bbbike.org/osm/bbbike/Corsica/Corsica.osm.gz)
- Downloading from BBBike
    1. Go to https://download.geofabrik.de/index.html and select a city or region.
    2. Get URL of *.osm.bz2* file (examplary URL: https://download.geofabrik.de/asia/maldives-latest.osm.bz2)


Downloading file from Geofabrik

In [29]:
target_filepath = tempname()
osm_file = download_geofabrik_file("https://download.geofabrik.de/asia/bhutan-latest.osm.bz2"; target_filepath = target_filepath)

File downloaded. Unzipping file...
File saved at 

/var/folders/k4/czzmds1d2yz83sv2728160680000gn/T/jl_9vVHGB.osm

"/var/folders/k4/czzmds1d2yz83sv2728160680000gn/T/jl_9vVHGB.osm"

Downloading file from BBBike

In [30]:
target_filepath = tempname()
osm_file = download_bbbike_file("https://download.bbbike.org/osm/bbbike/Singapore/Singapore.osm.gz"; target_filepath = target_filepath)

File downloaded. Unzipping file...
File saved at 

/var/folders/k4/czzmds1d2yz83sv2728160680000gn/T/jl_omSrTA.osm

"/var/folders/k4/czzmds1d2yz83sv2728160680000gn/T/jl_omSrTA.osm"

### 2. Generate a dataframe 
Generate a dataframe with the POI types defined in the parameters, based on `src/POITypes`. More information about the supported POI types by this API is provided in the documentation.

In [31]:
data = get_poi_df(osm_file, OSMgetPOI.POITypes.education_school, OSMgetPOI.POITypes.transport_busstop, OSMgetPOI.POITypes.cuisine_restaurant)

6813×7 DataFrame
  Row │ poi_type            lat      lon      addr:housenumber  addr:country   ⋯
      │ Any                 Any      Any      Any               Any            ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │ education_school    1.31934  103.745  698               SG             ⋯
    2 │ education_school    1.34098  103.952  11                SG
    3 │ education_school    1.2885   103.809  missing           missing       
    4 │ education_school    1.28493  103.829  missing           missing      
    5 │ education_school    1.35807  103.863  2C                SG             ⋯
    6 │ education_school    1.47666  103.745  missing           missing      
    7 │ education_school    1.39324  103.876  15                SG
    8 │ education_school    1.34786  103.718  missing           missing       
  ⋮   │         ⋮              ⋮        ⋮            ⋮               ⋮         ⋱
 6807 │ cuisine_restaurant  1.45655  103.764  missing           missing        ⋯
 6808 │ cuisine_restaurant  1.31224  103.923  missing           missing      
 6809 │ cuisine_restaurant  1.32122  103.887  missing           missing       
 6810 │ cuisine_restaurant  1.27906  103.845  missing           missing      
 6811 │ cuisine_restaurant  1.2802   103.847  198               SG             ⋯
 6812 │ cuisine_restaurant  1.30148  103.836  missing           missing       
 6813 │ cuisine_restaurant  1.30275  103.852  missing           missing       
                                                 2 columns and 6798 rows omitted

### 3. Save the results to a .csv file.

In [32]:
using CSV
CSV.write("output_csv/data.csv", data)

"output_csv/data.csv"

### 4. Visualising POIs on the map

In [33]:
using PyCall
using Colors
folium = pyimport("folium")

PyObject <module 'folium' from '/Users/marcinzurek/.julia/conda/3/lib/python3.9/site-packages/folium/__init__.py'>

In [34]:
m = folium.Map(location = [data.lat[1], data.lon[1]], zoom_start=11)
i = 1
for type_of_poi in unique(data.poi_type)
    colrs = distinguishable_colors(25, [RGB(1,0.6,0.5)])
    poi_color = "#$(hex(colrs[i]))"
    i += 1
    data_poi_type  = filter(row -> row.poi_type == type_of_poi, data)
    for i in 1:size(data_poi_type,1)
        street = data_poi_type[i,"addr:street"]
        number = data_poi_type[i, "addr:housenumber"]
        postcode = data_poi_type[i, "addr:postcode"]
        poi_type = type_of_poi
        folium.Circle(
            location = (data_poi_type.lat[i], data_poi_type.lon[i]),
            radius = 100,
            tooltip = "<b>POI: </b>$poi_type<br><br><b>Address</b><br>Street: $street<br>Number: $number<br>Postcode: $postcode",
            color = poi_color,
            fill = false,
            fill_color = poi_color
        ).add_to(m)
    end
end
m

PyObject <folium.folium.Map object at 0x1d7f24850>

### Remarks
This research was funded in whole or in part by [National Science Centre,  Poland][2021/41/B/HS4/03349]. For the software’s  documentation for the purpose of Open Access, the author has applied a CC-BY public copyright licence to any Author Accepted Manuscript (AAM) version arising from this submission.  
  
  
This Julia package is created by Marcin Zurek, Master Student @SGH Warsaw School of Economics and Przemyslaw Szufel, Assistant Professor @SGH Warsaw School of Economics